In [1]:
import pandas as pd
import ydata_profiling as pp
from pycaret.regression import *
pd.set_option('display.max_columns', None)

In [2]:
dataset = pd.read_csv("C:/Users/yunit/Downloads/data/processed_data.csv")
dataset = dataset.iloc[:2000]
dataset.head()

price  buildingSize  landSize  bedRooms  bathRooms  garages  \
0    850000000           100        50       3.0          2        0   
1   1700000000           110       103       3.0          2        0   
2   3500000000           201       113       3.0          4        1   
3  38000000000           600      1028       5.0          4        4   
4   1800000000           150       180       3.0          2        0   

          z    province               city    district  latitude  longitude  
0  1.324517  Jawa Timur           Surabaya  Tambaksari       NaN        NaN  
1  0.586065      Banten  Tangerang Selatan         NaN       NaN        NaN  
2  0.929438     Jakarta      Jakarta Timur    Matraman       NaN        NaN  
3  2.932825     Jakarta      Jakarta Pusat   Kemayoran       NaN        NaN  
4  0.586065  Jawa Timur           Sidoarjo    Sidoarjo       NaN        NaN

In [3]:
dataset.head(100)

price  buildingSize  landSize  bedRooms  bathRooms  garages  \
0     850000000           100        50       3.0          2        0   
1    1700000000           110       103       3.0          2        0   
2    3500000000           201       113       3.0          4        1   
3   38000000000           600      1028       5.0          4        4   
4    1800000000           150       180       3.0          2        0   
..          ...           ...       ...       ...        ...      ...   
95  18000000000           240       200       2.0          2        0   
96   4900000000           240       201       4.0          4        0   
97   4500000000             0        64       0.0          0        0   
98   1910000000           288       164       4.0          3        0   
99   9500000000           600       540       0.0          0        0   

           z    province               city        district  latitude  \
0   1.324517  Jawa Timur           Surabaya      Tambaksari       NaN   
1   0.586065      Banten  Tangerang Selatan             NaN       NaN   
2   0.929438     Jakarta      Jakarta Timur        Matraman       NaN   
3   2.932825     Jakarta      Jakarta Pusat       Kemayoran       NaN   
4   0.586065  Jawa Timur           Sidoarjo        Sidoarjo       NaN   
..       ...         ...                ...             ...       ...   
95  1.805030     Jakarta    Jakarta Selatan  Kebayoran Baru       NaN   
96  0.911963  Jawa Timur           Surabaya        Sukolilo       NaN   
97  5.183850     Jakarta      Jakarta Barat         Tambora       NaN   
98  0.770750  Jawa Barat            Bandung             NaN       NaN   
99  3.553027  Jawa Timur             Malang             NaN       NaN   

    longitude  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN  
..        ...  
95        NaN  
96        NaN  
97        NaN  
98        NaN  
99        NaN  

[100 rows x 12 columns]

In [13]:
prov = dataset[dataset['province'] == 'Sulawesi Selatan']
prov['city'].value_counts()

city
Makassar    9
Name: count, dtype: int64

In [5]:
data_train = dataset.sample(frac=0.8, random_state=110)
data_unseen = dataset.drop(data_train.index)

data_train.reset_index(drop=True, inplace=True)
data_unseen.reset_index(drop=True, inplace=True)

print('Data for train: ' + str(data_train.shape))
print('Data for test: ' +str(data_unseen.shape))

Data for train: (1600, 12)
Data for test: (400, 12)


In [14]:
profile = pp.ProfileReport(dataset)
profile.to_file('output.html')
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
cat_features = ['province', 'city']
exp = setup(data_train, target = 'price', categorical_features=cat_features, 
            ignore_features = ['z', 'district', 'latitude', 'longitude'], 
            numeric_imputation = 'mean', categorical_imputation= 'mode', 
            remove_outliers= True, normalize = True)

In [7]:
training_data = get_config(variable='X_train')
training_data

buildingSize  landSize  bedRooms  bathRooms  garages    province  \
783            550      1100       7.0          7        0        Bali   
602            300       240       4.0          4        0  Jawa Timur   
833            100       234       4.0          3        0  Jawa Barat   
50             240       276       3.0          2        0  Jawa Timur   
219            135       135       4.0          2        0  Jawa Timur   
...            ...       ...       ...        ...      ...         ...   
789             45        78       2.0          1        0  Jawa Barat   
1478            36        72       2.0          1        0  Jawa Timur   
993            140       120       3.0          2        0      Banten   
328            200       143       5.0          4        0     Jakarta   
171            130        90       4.0          3        0     Jakarta   

               city  
783         Gianyar  
602        Surabaya  
833          Bekasi  
50         Surabaya  
219        Surabaya  
...             ...  
789           Depok  
1478       Sidoarjo  
993       Tangerang  
328   Jakarta Barat  
171   Jakarta Timur  

[1120 rows x 7 columns]

In [8]:
best_model = compare_models()

In [9]:
#evaluate precition recall curve 
evaluate_model(best_model)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Pipeline Plot', 'pipelin…

In [10]:
predict_model(best_model, data = data_unseen)

buildingSize  landSize  bedRooms  bathRooms  garages         z  \
0             100        50       3.0          2        0  1.324517   
1             600      1028       5.0          4        4  2.932825   
2             140        70       3.0          2        0  0.923432   
3              70        80       2.0          2        0  1.003556   
4              50        91       2.0          1        0  1.166187   
..            ...       ...       ...        ...      ...       ...   
395           160       120       3.0          3        0  0.586065   
396           217       308       5.0          4        0  0.953334   
397           150       225       3.0          3        0  0.586065   
398            30        35       1.0          1        1  1.841519   
399            65        72       3.0          2        0  0.889756   

        province               city      district  latitude  longitude  \
0     Jawa Timur           Surabaya    Tambaksari       NaN        NaN   
1        Jakarta      Jakarta Pusat     Kemayoran       NaN        NaN   
2        Jakarta      Jakarta Pusat    Johar Baru       NaN        NaN   
3     Jawa Timur           Surabaya      Asemrowo       NaN        NaN   
4     Jawa Barat              Depok  Pancoran Mas       NaN        NaN   
..           ...                ...           ...       ...        ...   
395       Banten  Tangerang Selatan      BSD City       NaN        NaN   
396      Jakarta      Jakarta Timur        Cakung       NaN        NaN   
397   Jawa Barat            Bandung      Sukasari       NaN        NaN   
398  Jawa Tengah           Semarang     Tembalang       NaN        NaN   
399       Banten          Tangerang       Ciledug       NaN        NaN   

           price  prediction_label  
0      850000000      9.640911e+08  
1    38000000000      3.750893e+10  
2     1300000000      8.822269e+08  
3      550000000      9.647018e+08  
4      808000000      8.376700e+08  
..           ...               ...  
395   2250000000      2.490548e+09  
396   6250000000      4.075757e+09  
397   2300000000      2.694890e+09  
398    325000000      2.416229e+08  
399   1900000000      1.233055e+09  

[400 rows x 13 columns]

In [11]:
finalize_model(best_model)

Pipeline(memory=Memory(location=None),
         steps=[('numerical_imputer',
                 TransformerWrapper(include=['buildingSize', 'landSize',
                                             'bedRooms', 'bathRooms',
                                             'garages'],
                                    transformer=SimpleImputer())),
                ('categorical_imputer',
                 TransformerWrapper(include=['province', 'city'],
                                    transformer=SimpleImputer(strategy='most_frequent'))),
                ('onehot_encoding',
                 TransformerWrapper(incl...
                ('rest_encoding',
                 TransformerWrapper(include=['city'],
                                    transformer=TargetEncoder(cols=['city'],
                                                              handle_missing='return_nan'))),
                ('remove_outliers',
                 TransformerWrapper(transformer=RemoveOutliers(random_state=8051))),
                ('normalize', TransformerWrapper(transformer=StandardScaler())),
                ('actual_estimator',
                 <catboost.core.CatBoostRegressor object at 0x000002102F2D62D0>)])

In [12]:
save_model(best_model, 'property_pipeline')

Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=Memory(location=None),
          steps=[('numerical_imputer',
                  TransformerWrapper(include=['buildingSize', 'landSize',
                                              'bedRooms', 'bathRooms',
                                              'garages'],
                                     transformer=SimpleImputer())),
                 ('categorical_imputer',
                  TransformerWrapper(include=['province', 'city'],
                                     transformer=SimpleImputer(strategy='most_frequent'))),
                 ('onehot_encoding',
                  TransformerWrapper(incl...
                 ('rest_encoding',
                  TransformerWrapper(include=['city'],
                                     transformer=TargetEncoder(cols=['city'],
                                                               handle_missing='return_nan'))),
                 ('remove_outliers',
                  TransformerWrapper(transformer=RemoveOutliers(rand